In [1]:

import numpy as np
import supervision as sv
import cv2
print("supervision", sv.__version__)

supervision 0.18.0


In [2]:
from IPython import display
import glob
import os
import numpy as np
from itertools import combinations
import matplotlib.patches as patches
from collections import namedtuple
from collections import defaultdict
import matplotlib.pyplot as plt
import cv2
import sys
import math
import pandas as pd
from PIL import Image, ImageDraw, ImageFont
import argparse
import platform
import shutil
import time
from pathlib import Path
import logging
from typing import Callable, Generator, Optional, Tuple

# logging.getLogger().removeHandler(logging.getLogger().handlers[0])

import torch
import ultralytics

ultralytics.checks()
from ultralytics import YOLO

import supervision as sv
from supervision.draw.color import Color, ColorPalette

print("supervision", sv.__version__)


# import dev
from helpers.annotator import BoxAnnotator
from helpers.polygon_annotator import PolygonZoneAnnotator
from helpers.crossing_line import CrossingLine
from boxex import Boxes
from boxex import Results
from IPython import display
import dev
from icecream import ic

Ultralytics YOLOv8.1.14 🚀 Python-3.11.7 torch-2.2.0+cu121 CUDA:0 (NVIDIA GeForce RTX 3090, 24576MiB)
Setup complete ✅ (16 CPUs, 63.9 GB RAM, 7712.6/9314.0 GB disk)
supervision 0.18.0


In [3]:
print('torch.cuda.is_available(): ', torch.cuda.is_available())
print('torch.cuda.device_count(): ', torch.cuda.device_count())
print('torch.cuda.current_device(): ', torch.cuda.current_device())
print('torch.cuda.device(0): ', torch.cuda.device(0))
print('torch.cuda.get_device_name(0)": ', torch.cuda.get_device_name(0))
# setting device on GPU if available, else CPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)
print()
# Additional Info when using cuda
if device.type == "cuda":
    print(torch.cuda.get_device_name(0))
    print("Memory Usage:")
    print("Allocated:", round(torch.cuda.memory_allocated(0) / 1024**3, 1), "GB")
    print("Cached:   ", round(torch.cuda.memory_reserved(0) / 1024**3, 1), "GB")

torch.cuda.is_available():  True
torch.cuda.device_count():  1
torch.cuda.current_device():  0
torch.cuda.device(0):  <torch.cuda.device object at 0x00000226021FC910>
torch.cuda.get_device_name(0)":  NVIDIA GeForce RTX 3090
Using device: cuda

NVIDIA GeForce RTX 3090
Memory Usage:
Allocated: 0.0 GB
Cached:    0.0 GB


In [4]:
!nvidia-smi

Thu Mar 14 14:17:00 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 531.14                 Driver Version: 531.14       CUDA Version: 12.1     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                      TCC/WDDM | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf            Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA GeForce RTX 3090       WDDM | 00000000:01:00.0  On |                  N/A |
|  0%   57C    P8               40W / 350W|   1563MiB / 24576MiB |      9%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [5]:
import torch
!nvcc --version
TORCH_VERSION = ".".join(torch.__version__.split(".")[:2])
CUDA_VERSION = torch.__version__.split("+")[-1]
print("torch: ", TORCH_VERSION, "; cuda: ", CUDA_VERSION)

nvcc: NVIDIA (R) Cuda compiler drivertorch:  2.2 ; cuda:  cu121

Copyright (c) 2005-2023 NVIDIA Corporation
Built on Mon_Apr__3_17:36:15_Pacific_Daylight_Time_2023
Cuda compilation tools, release 12.1, V12.1.105
Build cuda_12.1.r12.1/compiler.32688072_0


In [6]:
import os
HOME = os.getcwd()
print(HOME)

e:\Traffic_


In [7]:
from IPython import display
display.clear_output()

import ultralytics
ultralytics.checks()

Ultralytics YOLOv8.1.14 🚀 Python-3.11.7 torch-2.2.0+cu121 CUDA:0 (NVIDIA GeForce RTX 3090, 24576MiB)
Setup complete ✅ (16 CPUs, 63.9 GB RAM, 7712.6/9314.0 GB disk)


In [8]:
from IPython import display
display.clear_output()



In [9]:
SOURCE_VIDEO= "E:/Traffic_/video/hiv.mp4"

In [10]:
from ultralytics import YOLO

model = YOLO('best.pt')

In [11]:
D = model.model.names

In [12]:
vehicle_tracking_ids = []
vehicle_count = {x:0 for x in list(model.model.names.keys())}

In [13]:
def drawing_on_frame_after_detection(frame):
    overlay = frame.copy()
    im0 = frame
    points_x = [[655, 40], [900, 40], [900, 70], [675, 70]]
    points_x = np.array(points_x)
    points_x = points_x.reshape((-1, 1, 2))
    # color = (255, 255, 255)
    thickness = 2
    isClosed = True
    cv2.fillPoly(overlay, [points_x], (0, 255, 0))
    alpha = 0.4
    im0 = cv2.addWeighted(overlay, alpha, frame, 1 - alpha, 0)

    frame = im0
    overlay = frame.copy()
    points_z = [[1267, 40], [1010, 40], [1010, 70], [1247, 70]]
    points_z = np.array(points_z)
    points_z = points_z.reshape((-1, 1, 2))
    # color = (255, 255, 255)
    thickness = 2
    isClosed = True
    cv2.fillPoly(overlay, [points_z], (0, 255, 0))
    alpha = 0.4
    frame = cv2.addWeighted(overlay, alpha, frame, 1 - alpha, 0)

    points = [
        [10, 10],
        [900, 10],
        [925, 30],
        [995, 30],
        [1020, 10],
        [1910, 10],
        [1910, 1070],
        [1020, 1070],
        [995, 1050],
        [925, 1050],
        [900, 1070],
        [10, 1070],
        [10, 10],
    ]
    points = np.array(points)
    points = points.reshape((-1, 1, 2))
    color = (255, 255, 255)
    thickness = 2
    isClosed = False
    cv2.polylines(frame, [points], isClosed, color, thickness)

    points_1 = [[30, 60], [60, 30], [800, 30]]
    points_1 = np.array(points_1)
    points_1 = points_1.reshape((-1, 1, 2))
    color = (255, 255, 255)
    thickness = 1
    isClosed = False
    cv2.polylines(frame, [points_1], isClosed, color, thickness)

    #######-------------------------------------------- 2nd RIGHT LINE -----------------------------------------------#######
    #######-------------------------------------------- 2nd RIGHT LINE -----------------------------------------------#######
    #######-------------------------------------------- 2nd RIGHT LINE -----------------------------------------------#######

    points_2 = [[1120, 30], [1860, 30], [1890, 60]]
    points_2 = np.array(points_2)
    points_2 = points_2.reshape((-1, 1, 2))
    color = (255, 255, 255)
    thickness = 1
    isClosed = False
    cv2.polylines(frame, [points_2], isClosed, color, thickness)

    #######-------------------------------------------- 3nd LEFT LINE -----------------------------------------------#######
    #######-------------------------------------------- 3nd LEFT LINE -----------------------------------------------#######
    #######-------------------------------------------- 3nd LEFT LINE -----------------------------------------------#######

    points_3 = [[500, 50], [650, 50], [670, 80], [900, 80]]
    points_3 = np.array(points_3)
    points_3 = points_3.reshape((-1, 1, 2))
    color = (255, 255, 255)
    thickness = 1
    isClosed = False
    cv2.polylines(frame, [points_3], isClosed, color, thickness)

    #######-------------------------------------------- 3nd RIGHT LINE -----------------------------------------------#######
    #######-------------------------------------------- 3nd RIGHT LINE -----------------------------------------------#######
    #######-------------------------------------------- 3nd RIGHT LINE -----------------------------------------------#######

    points_4 = [[1420, 50], [1270, 50], [1250, 80], [1020, 80]]
    points_4 = np.array(points_4)
    points_4 = points_4.reshape((-1, 1, 2))
    color = (255, 255, 255)
    thickness = 1
    isClosed = False
    cv2.polylines(frame, [points_4], isClosed, color, thickness)

    # cv2.putText(frame, "LOCATION - ", (800,60) ,0,0, 0.75, (255,255,255),2)
    font = cv2.FONT_HERSHEY_SIMPLEX

    # org
    org = (850, 60)
    # fontScale
    fontScale = 0.87
    # Blue color in BGR
    color = (255, 255, 255)
    # Line thickness of 2 px
    thickness = 2
    fontScale = 0.6
    thickness = 1

    #######-------------------------------------------- LATITUDE, LONGITUDE, DATA, TIME, ALTITUDE TEXT -----------------------------------------------#######
    #######-------------------------------------------- LATITUDE, LONGITUDE, DATA, TIME, ALTITUDE TEXT -----------------------------------------------#######
    #######-------------------------------------------- LATITUDE, LONGITUDE, DATA, TIME, ALTITUDE TEXT -----------------------------------------------#######

    font2 = ImageFont.truetype("font/Roboto-Bold.ttf", size=25)
    font3 = ImageFont.truetype("font/Roboto-Light.ttf", size=18)
    font4 = ImageFont.truetype("font/Depot Regular 400.ttf", size=18)
    font5 = ImageFont.truetype("font/Exo-Medium.ttf", size=16)

    frame = Image.fromarray(frame)
    draw = ImageDraw.Draw(frame, "RGBA")
    (x, y) = (500, 500)
    color = "rgb(0, 0, 0)"  # black color

    # Draw a rounded rectangle

    overlay = frame.copy()
    draw2 = ImageDraw.Draw(overlay)
    alpha = 0.5

    logo = cv2.imread("misc" + os.sep + "logo.png", cv2.IMREAD_UNCHANGED)

    draw.rounded_rectangle(
        (1690, 100, 1870, 200), fill=(0, 0, 0, 150), width=2, radius=15
    )
    draw.rounded_rectangle(
        (1690, 210, 1870, 310), fill=(0, 0, 0, 150), width=2, radius=15
    )
    draw.rounded_rectangle(
        (1690, 320, 1870, 420), fill=(0, 0, 0, 150), width=2, radius=15
    )
    draw.rounded_rectangle(
        (1690, 430, 1870, 530), fill=(0, 0, 0, 150), width=2, radius=15
    )

    draw.rounded_rectangle(
        (1580, 980, 1900, 1060), fill=(255, 255, 255, 150), width=2, radius=1
    )

    ht, wd = im0.shape[:2]

    # print("HT:::", ht)
    # print("WD:::", wd)

    # read overlay image
    # img2 = cv2.imread("sunglasses.png", cv2.IMREAD_UNCHANGED)
    ht2, wd2 = logo.shape[:2]

    # extract alpha channel as mask and base bgr images
    bgr = logo[:, :, 0:3]
    mask = logo[:, :, 3]

    # insert bgr into img at desired location and insert mask into black image
    x = 1600
    y = 1000

    bgr_new = im0.copy()
    bgr_new[y : y + ht2, x : x + wd2] = bgr

    mask_new = np.zeros((ht, wd), dtype=np.uint8)
    mask_new[y : y + ht2, x : x + wd2] = mask
    mask_new = cv2.cvtColor(mask_new, cv2.COLOR_GRAY2BGR)

    morph_kernel = np.zeros((3, 3), np.uint8)
    ret, mask_new = cv2.threshold(mask_new, 0, 255, cv2.THRESH_BINARY)

    # mask_new = cv2.dilate(mask_new,morph_kernel,iterations = 1)

    # overlay the base bgr image onto img using mask
    frame = np.where(mask_new == 255, bgr_new, frame)

    frame = Image.fromarray(frame)
    draw = ImageDraw.Draw(frame, "RGBA")
    overlay = frame.copy()
    draw2 = ImageDraw.Draw(overlay)

    # frame = np.array(frame)
    # ------------------------------------------------------------------------------------------------------------------------------------

    # draw.text((1730,120), format((groups[frame_num - 1]["time_stamp"])), fill=(255,255,255), font=font2)
    # draw.text((1760,165), "TIME", fill=(255,255,255), font=font3)

    # draw.text((1720,230), format((groups[frame_num - 1]["date"])), fill=(255,255,255), font=font2)
    # draw.text((1750,275), "DATE", fill=(255,255,255), font=font3)

    # draw.text((1752,340), format((groups[frame_num - 1]["iso"])), fill=(255,255,255), font=font2)
    # draw.text((1760,385), "ISO", fill=(255,255,255), font=font3)

    # draw.text((1745,450), format((groups[frame_num - 1]["shutter"])), fill=(255,255,255), font=font2)
    # draw.text((1748,495), "SHUTTER", fill=(255,255,255), font=font3)

    # draw.text((775,45), format((groups[frame_num - 1]["latitude"])), fill=(0,0,0), font=font5)
    # draw.text((680,45), "LATITUDE: ", fill=(0,0,0), font=font5)

    # draw.text((1130,45), format((groups[frame_num - 1]["longitude"])), fill=(0,0,0), font=font5)
    # draw.text((1020,45), "LONGITUDE: ", fill=(0,0,0), font=font5)

    frame = np.array(frame)

    font2 = ImageFont.truetype("font/Roboto-Bold.ttf", size=25)
    font3 = ImageFont.truetype("font/Roboto-Light.ttf", size=18)
    font4 = ImageFont.truetype("font/Depot Regular 400.ttf", size=20)
    font5 = ImageFont.truetype("font/Exo-Medium.ttf", size=17)
    font6 = ImageFont.truetype("font/Exo-Medium.ttf", size=14)
    # font5 = ImageFont.truetype('Terrabyte-Regular.ttf', size=15)

    frame = Image.fromarray(frame)
    draw = ImageDraw.Draw(frame, "RGBA")

    color = "rgb(0, 0, 0)"  # black color

    overlay = frame.copy()
    draw2 = ImageDraw.Draw(overlay)
    alpha = 0.5

    draw.rectangle((45, 91, 250, 790), fill=(92, 11, 249, 100), width=2)
    # draw.rectangle((45, 90,48,780), fill=(255,255,255, 255),width=2)
    # draw.rectangle((45, 87,375,140), fill=(0,0,0, 255),width=2)

    draw.rectangle((250, 91, 305, 790), fill=(131, 30, 239, 100), width=2)

    draw.rectangle((305, 91, 375, 790), fill=(162, 45, 230, 100), width=2)

    # draw.rectangle((45, 55,375,105), fill=(92,11,249, 150),width=2)

    # ------------------------------------
    # draw.rectangle((45, 91,250,720), fill=(92,11,249, 100),width=2)
    draw.rectangle((45, 90, 48, 790), fill=(255, 255, 255, 255), width=2)
    draw.rectangle((45, 87, 375, 90), fill=(0, 0, 0, 255), width=2)

    # draw.rectangle((250, 91,305,720), fill=(131,30,239, 100),width=2)

    # draw.rectangle((305, 91,375,720), fill=(162,45,230, 100),width=2)

    draw.rectangle((45, 55, 375, 85), fill=(92, 11, 249, 150), width=2)

    draw.text((70, 62), "VEHICLE TYPE", fill=(255, 255, 255), font=font4)
    draw.text((250, 62), "COUNT", fill=(255, 255, 255), font=font4)
    # draw.text((320, 62), "AREA", fill=(255, 255, 255), font=font4)


    global vehicle_count
    index_list = [idx for idx, val in enumerate(list(vehicle_count.values())) if val != 0]
    filtered_classes = [list(model.model.names.values())[x] for x in index_list]
    filtered_count = [list(vehicle_count.values())[x] for x in index_list]


    x = 60
    [
        draw.text(
            (x, 100 + i * 30),
            label,
            fill=(250, 250, 250),
            font=font6 if len(label) > 20 else font5,
        )
        # to show all classes names
        # for i, label in enumerate(list(model.model.names.values()))
        for i, label in enumerate(filtered_classes)
    ]
    x_off = 270
    [
        draw.text(
            (x_off, 100 + i * 30),
            str(v_count),
            fill=(255, 255, 255),
            font=font5,
        )
        # to show all classes count
        # for i,v_count in enumerate(list(vehicle_count.values()))
        for i,v_count in enumerate(filtered_count)
    ]


    frame = np.array(frame)
    return frame

In [14]:
def show_frames_into_video_final(frame):
    cv2.imshow(SOURCE_VIDEO, frame)
    if cv2.waitKey(5) & 0xFF == ord("q"):
        cv2.destroyAllWindows()

In [15]:
# def draw_labels(model, detections):
#         labels = [f"{tracker_id} {model.model.names[class_id]} {confidence:0.2f}"
#                 for _,_, confidence, class_id, tracker_id,_ 
#                 in detections]
#         # labels = [f"{model.names[class_id]} {confidence:0.2f}" for _,_,confidence, class_id,_,_ in detections]
#         return labels

def draw_labels(detections):
        labels = [f"{tracker_id} {model.model.names[class_id]} {confidence:0.2f}"
                for _,_, confidence, class_id, tracker_id,_ 
                in detections]
        # labels = [f"{model.names[class_id]} {confidence:0.2f}" for _,_,confidence, class_id,_,_ in detections]
        return labels

In [16]:
video_info = sv.VideoInfo.from_video_path(SOURCE_VIDEO)

In [17]:
from helpers.crossing_line import CrossingLine
import pandas as pd

In [18]:
crossing_line = CrossingLine()
cross_line = [np.array([[334, 710],[838, 726]])]
cross_line

[array([[334, 710],
        [838, 726]])]

In [19]:
# Anotating boundryboxes of the detected objects in an the input video
# polygon_zones = [np.array([(196, 806), (596, 554), (896, 546), (796, 854)])]
polygon_zones = [
np.array([
[42, 704],[666, 456],[1270, 452],[1862, 712]
])
]

polygon_zone_annotators = [
    PolygonZoneAnnotator(
        # color=Color.YELLOW,
        thickness=5,
        text_thickness=2,
        text_scale=1,
    )
    for index in range(len(polygon_zones))
]

box_annotators = [
    BoxAnnotator(
        # color=colors.by_idx(index),
        thickness=4,
        text_thickness=2,
        text_scale=0.7,
    )
    for index in range(len(polygon_zones))
]


def bounding_box_annotator(frame, detections):
    # box annotator without filtering and tracking
    for box_annotator in box_annotators:
        labels = [
            f"#{tracker_id} {model.names[class_id]} {confidence:0.2f}"
            for _, _, confidence, class_id, tracker_id, _ in detections
        ]
        frame = box_annotator.annotate(
            scene=frame, detections=detections, labels=labels
        )
    return frame


In [20]:

video_info = sv.VideoInfo.from_video_path(SOURCE_VIDEO)

In [21]:
def polygon_zones_interestd(frame, detections):
    # polygon zones annotator
    for zone_annotator in polygon_zone_annotators:
        labels = []
        mask = zone_annotator.trigger(
            polygon_zones=polygon_zones, detections=detections
        )
        filtered_zone_detections = detections[mask]

        # TODO below both zone annotations will be removed in production (zone boundary and interested zone should not be plotted but will be used for counting and area calculation)
        frame = zone_annotator.annotate(
            scene=frame, polygon_zones=polygon_zones, labels=labels, color=Color.YELLOW.as_bgr()
        )
    return frame, filtered_zone_detections

In [22]:
def bb_intersection_over_union(boxA, boxB):
	# determine the (x, y)-coordinates of the intersection rectangle
	xA = max(boxA[0], boxB[0])
	yA = max(boxA[1], boxB[1])
	xB = min(boxA[2], boxB[2])
	yB = min(boxA[3], boxB[3])
	# compute the area of intersection rectangle
	interArea = max(0, xB - xA + 1) * max(0, yB - yA + 1)
	# compute the area of both the prediction and ground-truth
	# rectangles
	boxAArea = (boxA[2] - boxA[0] + 1) * (boxA[3] - boxA[1] + 1)
	boxBArea = (boxB[2] - boxB[0] + 1) * (boxB[3] - boxB[1] + 1)
	# compute the intersection over union by taking the intersection
	# area and dividing it by the sum of prediction + ground-truth
	# areas - the interesection area
	iou = interArea / float(boxAArea + boxBArea - interArea)
	# return the intersection over union value
	return iou

In [23]:
list_vehicle = [
        'Car',
        'Cycle',
        'MotorCycle',
        'Jeep',
        'Road_Roller',
        'Excavator',
        'Bus',
        'Three_wheeler',
        'Van',
        'Van_Ambulance',
        'G1_Pickup',
        'G2_Mini_Truck',
        'G10_2_Axle_Rigid_Truck',
        'G11_3_Axle_Rigid_Truck',
        'G12_Tandem_Axles_Truck',
        'Gx3_3_Axle_Articulated_Truck',
        'Gx4_4_Axle_Articulated_Truck',
        'Gx5_5_Axle_Articulated_Truck',
        'Gx6_6_Axle_Articulated_Truck',
        'LG1_Mini_Tanker',
        'LG10_2_Axle_Rigid_Tanker',
        'LG11_3_Axle_Rigid_Tanker',
        'LGx3_3_Axle_Articulated_Tanker',
        'LGx4_4_Axle_Articulated_Tanker',
        'LGx5_5_Axle_Articulated_Tanker',
        'LGx6_6_Axle_Articulated_Tanker',
        'GV10_2_Axle_Rigid_Motorbike_Carrier',
        'GV11_3_Axle_Rigid_Motorbike_Carrier',
        'GVx4_Articulated_Car_Carrier',
        'GV3W_Rigid_Wide_Bed',
        'GVx5_6w_Articulated_Wide_Bed',
        'RVxS_Super_Truck',
        'R1beG_Tractor_Trolley_Tanker'
]
dict_vehicle = {}


# def count_objects_(frame, detections):
#     tracking_id = detections.tracker_id
#     class_id = detections.class_id
#     if tracking_id is None:
#         return 
#     for i in range(len(tracking_id)):
#         print("Tracking ID",tracking_id[i])
#         print("Class ID",class_id[i])
#     return frame

In [24]:
crossing_line = CrossingLine()
cross_line = [np.array([[334, 710],[838, 726]])]
cross_line

[array([[334, 710],
        [838, 726]])]

In [25]:
CLASS_NAMES_DICT = model.model.names

In [26]:
# Last
# def count_objects_(frame, objects_in_polygone_zone):

#     global vehicle_tracking_ids, vehicle_count
#     dict_ = {}

#     tracking_id = objects_in_polygone_zone.tracker_id
#     confidence_ = objects_in_polygone_zone.confidence
#     cls_id =  objects_in_polygone_zone.class_id
#     classesss = model.names
#     print("Tracking IDS: ", tracking_id)
#     print('Confidence: ', confidence_)
#     print("Class name: ", classesss)
#     print("Class id: ", cls_id)
#     if tracking_id is not None:
#         for i in range(len(objects_in_polygone_zone)):
#             if objects_in_polygone_zone.tracker_id[i] not in vehicle_tracking_ids:
#                 vehicle_tracking_ids.append(objects_in_polygone_zone.tracker_id[i])
                
#                 if (confidence_[i] > 0.90)  and cls_id[i] in vehicle_tracking_ids:
#                     # vehicle_tracking_ids.append(objects_in_polygone_zone.tracker_id[i])
#                     vehicle_count[objects_in_polygone_zone.class_id[i]] -= 1 
#                 else:
#                     confidence_[i] > 0.90  and objects_in_polygone_zone.class_id[i] and objects_in_polygone_zone.tracker_id[i] not in vehicle_tracking_ids
#                     vehicle_tracking_ids.append(objects_in_polygone_zone.tracker_id[i])
#                     # print('vehicle_tracking_idssssssssssss: ', vehicle_tracking_ids)
#                     vehicle_count[objects_in_polygone_zone.class_id[i]] += 1
#         # print('vehicle_tracking_ids: ', vehicle_tracking_ids)
#         dev.print_dict(vehicle_count)

#     cv2.putText(frame, f'Count: {len(vehicle_tracking_ids)}', (500, 500), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 0, 0), 2, cv2.LINE_AA)
    
#     return frame

In [27]:

# dict_ = {}
# def count_objects_(frame, objects_in_polygone_zone):

#     global vehicle_tracking_ids, vehicle_count, dict_

#     tracking_id = objects_in_polygone_zone.tracker_id
#     confidence_ = objects_in_polygone_zone.confidence
#     cls_id =  objects_in_polygone_zone.class_id
#     classesss = model.names
#     if tracking_id is not None:
#         for i in range(len(objects_in_polygone_zone)):
#             if objects_in_polygone_zone.tracker_id[i] not in vehicle_tracking_ids:
#                 vehicle_tracking_ids.append(objects_in_polygone_zone.tracker_id[i])
#                 vehicle_count[objects_in_polygone_zone.class_id[i]] += 1
#         print('vehicle_tracking_ids: ', vehicle_tracking_ids)
#         dev.print_dict(vehicle_count)

#     cv2.putText(frame, f'Count: {len(vehicle_tracking_ids)}', (500, 500), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 0, 0), 2, cv2.LINE_AA)
    
#     return frame


dictionary  = {}

def count_objects_(frame, objects_in_polygone_zone, frame_number):
    global dictionary, vehicle_count

    tracking_id = objects_in_polygone_zone.tracker_id
    confidence = objects_in_polygone_zone.confidence
    cls_id =  objects_in_polygone_zone.class_id
    classesss = model.names
    print(dev.print_dict(dictionary))
    if tracking_id is not None:
        for i in range(len(objects_in_polygone_zone)):
            print('start----> tracking_id[i]: ', tracking_id[i])
            if tracking_id[i] not in dictionary:
                dictionary[tracking_id[i]]= [cls_id[i], confidence[i]]
                print('if tracking_id[i] not in dictionary:-------\n')
                print('[cls_id[i], confidence[i]]: ', [cls_id[i], confidence[i]])
                print('dictionary[tracking_id[i]]: ', dictionary[tracking_id[i]])
                print()
            elif tracking_id[i] in dictionary:
                previous_cls = dictionary[tracking_id[i]][0]
                previous_conf = dictionary[tracking_id[i]][1]
                print('elif  tracking_id[i] in dictionary:--------\n')
                print('tracking_id: ', tracking_id[i])
                print('previous_cls: ', previous_cls)
                print('current_cls : ', cls_id[i])
                print('previous_conf: ', previous_conf)
                print('current_conf : ', confidence[i])
                print()
                if previous_cls == cls_id[i] and previous_conf <  confidence[i]:
                    ic()
                    dictionary[tracking_id[i]][1] = confidence[i]
                elif  previous_cls != cls_id[i] and previous_conf <  confidence[i]:
                    ic()
                    dictionary[tracking_id[i]][0] = cls_id[i]
                    dictionary[tracking_id[i]][1] = confidence[i]

    cv2.putText(frame, f'frame:{frame_number} Count: {len(dictionary)}', (500, 500), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 0, 0), 2, cv2.LINE_AA)

    lst = [x[0] for x in dictionary.values()]
    from collections import Counter
    count_dict = dict(Counter(lst))
    vehicle_count = {x:0 for x in list(model.model.names.keys())}
    for i in count_dict:
        vehicle_count[i] = count_dict[i]
    print("vehicle_count----> ",vehicle_count)
    print(dev.print_dict(dictionary))
    print('-'*50)
    return frame

In [28]:
print(type(vehicle_tracking_ids))

<class 'list'>


In [29]:
model.names.values()

dict_values(['Car', 'Cycle', 'Bike', 'Jeep', 'Road Roller', 'Excavator', 'Bus', 'Three wheeler', 'Van', 'Van(Ambulance)', 'G1(Pickup)', 'G2(Mini Truck)', 'G10(2-Axle Rigid Truck)', 'G11(3-Axle Rigid Truck)', 'G12(Tandem Axles Truck)', 'Gx3(3-Axle Articulated Truck)', 'Gx4(4-Axle Articulated Truck)', 'Gx5(5-Axle Articulated Truck)', 'Gx6(6-Axle Articulated Truck)', 'LG1(Mini Tanker)', 'LG10(2-Axle Rigid Tanker)', 'LG11(3-Axle Rigid Tanker)', 'LGx3(3-Axle Articulated Tanker)', 'LGx4(4-Axle Articulated Tanker)', 'LGx5(5-Axle Articulated Tanker)', 'LGx6(6-Axle Articulated Tanker)', 'GV10(2-Axle Rigid Motorbike Carrier)', 'GV11(3-Axle Rigid Motorbike Carrier)', 'GVx4(Articulated Car Carrier)', 'GV3W(Rigid Wide Bed)', 'GVx5/6w(Articulated Wide Bed)', 'RVxS(Super Truck)', 'R1beG(Tractor Trolley/Tanker)'])

In [30]:
temp1 = None

In [31]:
def save_video_frames(frame_id=None, det_original=None, det_tracking=None):
    if det_original is not None:
        path = "det_original" + os.sep + str(frame_id) + ".jpg"
    elif det_tracking is not None:
        pp = "det_tracking"
        if not os.path.exists(pp):
            os.mkdir(pp)
        path = pp + os.sep + str(frame_id) + ".jpg"
        cv2.imwrite(path, det_tracking)

In [32]:
def process_frame(frame: np.ndarray, frame_number) -> np.ndarray:
    print(frame_number)
    results = model.track(frame, show= True,persist= True,agnostic_nms=True, device=0)[0]
    detections = sv.Detections.from_ultralytics(results)
    # if detections.tracker_id is None:
    #     return frame

    global temp1
    temp1 = detections
    frame, filtered_zone_detections = polygon_zones_interestd(frame, detections)
    frame = bounding_box_annotator(frame, filtered_zone_detections)


    frame = count_objects_(frame, filtered_zone_detections, frame_number)

    # count += filtered_zone_detections.tracker_id

    # print(filtered_zone_detections, count)

    # frame = crossing_line.annotate(frame, cross_line)

    # count_objects_in_zone(filtered_zone_detections, classes)
    frame = drawing_on_frame_after_detection(frame)

    # print("FRame: ", frame)
    # frame = box_annotator.annotate(scene=frame, detections=detections, labels=labels)
    # frame = zone_annotator.annotate(scene=frame)
    show_frames_into_video_final(frame)
    save_video_frames(frame_id=frame_number, det_tracking=frame)
    print('_______________________________________________________________________________________')
    # if frame_number % 100 == 0:
    #     display.clear_output()
    return frame

In [33]:
sv.process_video(source_path=SOURCE_VIDEO,target_path= "_result.mp4", callback=process_frame)
cv2.destroyAllWindows()

0



0: 384x640 8 Cars, 2 Vans, 1 G2(Mini Truck), 101.6ms
Speed: 3.0ms preprocess, 101.6ms inference, 2.0ms postprocess per image at shape (1, 3, 384, 640)
start----> tracking_id[i]:  1
if tracking_id[i] not in dictionary:-------

[cls_id[i], confidence[i]]:  [11, 0.93030286]
dictionary[tracking_id[i]]:  [11, 0.93030286]

start----> tracking_id[i]:  2
if tracking_id[i] not in dictionary:-------

[cls_id[i], confidence[i]]:  [0, 0.922915]
dictionary[tracking_id[i]]:  [0, 0.922915]

start----> tracking_id[i]:  4
if tracking_id[i] not in dictionary:-------

[cls_id[i], confidence[i]]:  [0, 0.91400516]
dictionary[tracking_id[i]]:  [0, 0.91400516]

start----> tracking_id[i]:  5
if tracking_id[i] not in dictionary:-------

[cls_id[i], confidence[i]]:  [0, 0.9090306]
dictionary[tracking_id[i]]:  [0, 0.9090306]

start----> tracking_id[i]:  6
if tracking_id[i] not in dictionary:-------

[cls_id[i], confidence[i]]:  [8, 0.9062505]
dictionary[tracking_id[i]]:  [8, 0.9062505]

start----> tracking_id[i

ic| 2117298335.py:53 in count_objects_() at 14:17:04.857
ic| 2117298335.py:53 in count_objects_() at 14:17:04.876
ic| 2117298335.py:53 in count_objects_() at 14:17:04.892
ic| 2117298335.py:53 in count_objects_() at 14:17:04.906


start----> tracking_id[i]:  6
elif  cls_id[i] in dictionary:--------

tracking_id:  6
previous_cls:  8
current_cls :  8
previous_conf:  0.9062505
current_conf :  0.9111967

start----> tracking_id[i]:  7
elif  cls_id[i] in dictionary:--------

tracking_id:  7
previous_cls:  0
current_cls :  0
previous_conf:  0.8614682
current_conf :  0.86299765

start----> tracking_id[i]:  8
elif  cls_id[i] in dictionary:--------

tracking_id:  8
previous_cls:  0
current_cls :  0
previous_conf:  0.85276663
current_conf :  0.860796

start----> tracking_id[i]:  9
elif  cls_id[i] in dictionary:--------

tracking_id:  9
previous_cls:  0
current_cls :  0
previous_conf:  0.80749667
current_conf :  0.7927173

start----> tracking_id[i]:  10
elif  cls_id[i] in dictionary:--------

tracking_id:  10
previous_cls:  0
current_cls :  0
previous_conf:  0.79375744
current_conf :  0.80312765



ic| 2117298335.py:53 in count_objects_() at 14:17:04.922


...

 93
elif  cls_id[i] in dictionary:--------

tracking_id:  93
previous_cls:  0
current_cls :  0
previous_conf:  0.90450764
current_conf :  0.58888775

start----> tracking_id[i]:  94
elif  cls_id[i] in dictionary:--------

tracking_id:  94
previous_cls:  0
current_cls :  0
previous_conf:  0.92679656
current_conf :  0.8085817

start----> tracking_id[i]:  96
elif  cls_id[i] in dictionary:--------

tracking_id:  96
previous_cls:  3
current_cls :  0
previous_conf:  0.95875984
current_conf :  0.6616283

start----> tracking_id[i]:  97
elif  cls_id[i] in dictionary:--------

tracking_id:  97
previous_cls:  0
current_cls :  0
previous_conf:  0.92446595
current_conf :  0.8212447

start----> tracking_id[i]:  98
elif  cls_id[i] in dictionary:--------

tracking_id:  98
previous_cls:  0
current_cls :  0
previous_conf:  0.91979223
current_conf :  0.8261414

start----> tracking_id[i]:  102
elif  cls_id[i] in dictionary:--------

tracking_id:  102
previous_cls:  0
current_cls :  0
previous_conf:  0.9200

ic| 2117298335.py:53 in count_objects_() at 14:20:40.012


start----> tracking_id[i]:  93
elif  cls_id[i] in dictionary:--------

tracking_id:  93
previous_cls:  0
current_cls :  0
previous_conf:  0.90450764
current_conf :  0.4049334

start----> tracking_id[i]:  94
elif  cls_id[i] in dictionary:--------

tracking_id:  94
previous_cls:  0
current_cls :  0
previous_conf:  0.92679656
current_conf :  0.8159887

start----> tracking_id[i]:  96
elif  cls_id[i] in dictionary:--------

tracking_id:  96
previous_cls:  3
current_cls :  0
previous_conf:  0.95875984
current_conf :  0.6800512

start----> tracking_id[i]:  97
elif  cls_id[i] in dictionary:--------

tracking_id:  97
previous_cls:  0
current_cls :  0
previous_conf:  0.92446595
current_conf :  0.81138897

start----> tracking_id[i]:  98
elif  cls_id[i] in dictionary:--------

tracking_id:  98
previous_cls:  0
current_cls :  0
previous_conf:  0.91979223
current_conf :  0.8153109

start----> tracking_id[i]:  102
elif  cls_id[i] in dictionary:--------

tracking_id:  102
previous_cls:  0
current_cls 

ic| 2117298335.py:53 in count_objects_() at 14:20:40.464


start----> tracking_id[i]:  93
elif  cls_id[i] in dictionary:--------

tracking_id:  93
previous_cls:  0
current_cls :  0
previous_conf:  0.90450764
current_conf :  0.74751574

start----> tracking_id[i]:  94
elif  cls_id[i] in dictionary:--------

tracking_id:  94
previous_cls:  0
current_cls :  0
previous_conf:  0.92679656
current_conf :  0.82830054

start----> tracking_id[i]:  96
elif  cls_id[i] in dictionary:--------

tracking_id:  96
previous_cls:  3
current_cls :  0
previous_conf:  0.95875984
current_conf :  0.78658056

start----> tracking_id[i]:  97
elif  cls_id[i] in dictionary:--------

tracking_id:  97
previous_cls:  0
current_cls :  0
previous_conf:  0.92446595
current_conf :  0.824092

start----> tracking_id[i]:  98
elif  cls_id[i] in dictionary:--------

tracking_id:  98
previous_cls:  0
current_cls :  0
previous_conf:  0.91979223
current_conf :  0.8252657

start----> tracking_id[i]:  102
elif  cls_id[i] in dictionary:--------

tracking_id:  102
previous_cls:  0
current_cls

In [34]:
list_vehicle = [
        'Car',
        'Cycle',
        'MotorCycle',
        'Jeep',
        'Road_Roller',
        'Excavator',
        'Bus',
        'Three_wheeler',
        'Van',
        'Van_Ambulance',
        'G1_Pickup',
        'G2_Mini_Truck',
        'G10_2_Axle_Rigid_Truck',
        'G11_3_Axle_Rigid_Truck',
        'G12_Tandem_Axles_Truck',
        'Gx3_3_Axle_Articulated_Truck',
        'Gx4_4_Axle_Articulated_Truck',
        'Gx5_5_Axle_Articulated_Truck',
        'Gx6_6_Axle_Articulated_Truck',
        'LG1_Mini_Tanker',
        'LG10_2_Axle_Rigid_Tanker',
        'LG11_3_Axle_Rigid_Tanker',
        'LGx3_3_Axle_Articulated_Tanker',
        'LGx4_4_Axle_Articulated_Tanker',
        'LGx5_5_Axle_Articulated_Tanker',
        'LGx6_6_Axle_Articulated_Tanker',
        'GV10_2_Axle_Rigid_Motorbike_Carrier',
        'GV11_3_Axle_Rigid_Motorbike_Carrier',
        'GVx4_Articulated_Car_Carrier',
        'GV3W_Rigid_Wide_Bed',
        'GVx5_6w_Articulated_Wide_Bed',
        'RVxS_Super_Truck',
        'R1beG_Tractor_Trolley_Tanker'
]
# dict_vehicle = { i:0 for i in list_vehicle}

# Dictionary with car names as keys and initial values as None
dict_vehicle = {car_name: None for car_name in list_vehicle}

# Printing the dictionary
# print(dict_vehicle)

In [35]:
import numpy as np

# Creating a NumPy array
np_array = np.array([1, 2, 3, 4, 5, 2, 3])

# Creating an empty dictionary
my_dict = {}
seen_values = set()

# Adding NumPy array values to the dictionary
for value in np_array:
    if value not in seen_values:
        my_dict[f'key_{value}'] = value
        seen_values.add(value)

print(seen_values)


{1, 2, 3, 4, 5}
